In [1]:
import sys
import os
import tensorflow as tf

sys.path.append(os.path.abspath(".."))

import config

Used for Art dataset

In [ ]:
class NestedImageResizer_Art:
    def __init__(self, input_dir, output_dir):
        """
        Initialize the image resizer using global config parameters.
        
        Args:
            input_dir (str): Directory containing the 'fake' and 'real' subdirectories.
            output_dir (str): Directory to save the resized images.
        """
        self.input_dir = input_dir
        self.output_dir = output_dir

        self.fake_dir = os.path.join(input_dir, "fake")
        self.real_dir = os.path.join(input_dir, "real")

        os.makedirs(os.path.join(output_dir, "fake"), exist_ok=True)
        os.makedirs(os.path.join(output_dir, "real"), exist_ok=True)

    def _list_images(self, directory):
        """
        Recursively list all image files in a directory.
        
        Args:
            directory (str): Root directory to search for images.
        
        Returns:
            list: Full paths to image files.
        """
        image_paths = []
        for root, _, files in os.walk(directory):
            for file in files:
                if file.lower().endswith(('.png', '.jpg', '.jpeg', '.bmp', '.gif')):
                    image_paths.append(os.path.join(root, file))
        return image_paths

    def _parse_and_resize_image(self, filename):
        """
        Read and resize an image from the given filename.
        
        Args:
            filename (str): Path to the image file.
        
        Returns:
            tf.Tensor: Resized image tensor in uint8.
        """
        image_raw = tf.io.read_file(filename)
        image = tf.image.decode_image(image_raw, channels=3)

        image = tf.image.resize(image, config.IMG_SIZE)

        image = tf.clip_by_value(image, 0, 255)
        image = tf.cast(image, tf.uint8)
        return image

    def _save_resized_image(self, image, output_path):
        """
        Encode the image in JPEG format and write it to disk.
        
        Args:
            image (tf.Tensor): Image tensor to save.
            output_path (str): Path where the resized image will be stored.
        """
        encoded_image = tf.io.encode_jpeg(image)
        tf.io.write_file(output_path, encoded_image)

    def resize_and_save_images(self, max_images_per_class=None):
        """
        Resize images from both 'fake' and 'real' classes and save them to the output directory.
        
        Args:
            max_images_per_class (int, optional): Optionally limit the number of images processed per class.
        """
        # List images in both class directories
        fake_images = self._list_images(self.fake_dir)
        real_images = self._list_images(self.real_dir)

        if max_images_per_class:
            fake_images = fake_images[:max_images_per_class]
            real_images = real_images[:max_images_per_class]

        print(
            f"Processing {len(fake_images)} fake images and {len(real_images)} real images.")

        # fake images
        for file_path in fake_images:
            try:
                image = self._parse_and_resize_image(file_path)
                file_name = os.path.basename(file_path)
                output_path = os.path.join(self.output_dir, "fake", file_name)
                self._save_resized_image(image, output_path)
                print(f"Saved resized fake image to {output_path}")
            except Exception as e:
                print(f"Error processing {file_path}: {e}")

        # real images
        for file_path in real_images:
            try:
                image = self._parse_and_resize_image(file_path)
                file_name = os.path.basename(file_path)
                output_path = os.path.join(self.output_dir, "real", file_name)
                self._save_resized_image(image, output_path)
                print(f"Saved resized real image to {output_path}")
            except Exception as e:
                print(f"Error processing {file_path}: {e}")


if __name__ == "__main__":
    resizer = NestedImageResizer_Art(
        input_dir=config.DATA_DIR, output_dir=config.OUTPUT_DIR)
    resizer.resize_and_save_images()

Used for Faces dataset

In [2]:
class NestedImageResizer_Face:
    def __init__(self, input_dir, output_dir, img_size=(200, 200)):
        """
        Initialize the image resizer to process fake and real images.

        Args:
            input_dir (str): Path to the 'data' directory.
            output_dir (str): Path to save resized images in '0' and '1' folders.
            img_size (tuple): Target image size (height, width).
        """
        self.input_dir = input_dir
        self.output_dir = output_dir
        self.img_size = img_size

        self.fake_root = os.path.join(input_dir, "fake")
        self.real_root = os.path.join(input_dir, "ffhq")

        os.makedirs(os.path.join(output_dir, "1"), exist_ok=True)  # fake
        os.makedirs(os.path.join(output_dir, "0"), exist_ok=True)  # real

    def _list_images(self, directory):
        image_paths = []
        for root, _, files in os.walk(directory):
            for file in files:
                if file.lower().endswith(('.png', '.jpg', '.jpeg', '.bmp', '.gif')):
                    full_path = os.path.join(root, file)
                    image_paths.append(full_path)
        print(f"Found {len(image_paths)} images in {directory}")
        return image_paths

    def _parse_and_resize_image(self, filename):
        image_raw = tf.io.read_file(filename)
        image = tf.image.decode_image(image_raw, channels=3)
        image.set_shape([None, None, 3])  # Ensure shape is set for resizing
        image = tf.image.resize(image, self.img_size)
        image = tf.clip_by_value(image, 0, 255)
        image = tf.cast(image, tf.uint8)
        return image

    def _save_resized_image(self, image, output_path):
        encoded_image = tf.io.encode_jpeg(image)
        tf.io.write_file(output_path, encoded_image)

    def resize_and_save_images(self, max_images_per_class=None):
        fake_images = self._list_images(self.fake_root)
        real_images = self._list_images(self.real_root)

        if max_images_per_class:
            fake_images = fake_images[:max_images_per_class]
            real_images = real_images[:max_images_per_class]

        print(f"Processing {len(fake_images)} fake images and {len(real_images)} real images...")

        # Process fake images → label "1"
        for file_path in fake_images:
            try:
                image = self._parse_and_resize_image(file_path)
                file_name = os.path.basename(file_path)
                output_path = os.path.join(self.output_dir, "1", file_name)
                self._save_resized_image(image, output_path)
                print(f"Saved resized fake image to {output_path}")
            except Exception as e:
                print(f"Error processing {file_path}: {e}")

        # Process real images → label "0"
        for file_path in real_images:
            try:
                image = self._parse_and_resize_image(file_path)
                file_name = os.path.basename(file_path)
                output_path = os.path.join(self.output_dir, "0", file_name)
                self._save_resized_image(image, output_path)
                print(f"Saved resized real image to {output_path}")
            except Exception as e:
                print(f"Error processing {file_path}: {e}")

In [3]:
resizer = NestedImageResizer_Face(
    input_dir="../data",
    output_dir="../data_resized"
)
resizer.resize_and_save_images()

Found 50959 images in ../data/fake
Found 70000 images in ../data/ffhq
Processing 50959 fake images and 70000 real images...
Saved resized fake image to ../data_resized/1/0224b1faa72b379b5f06cc0b30e6cf56da0b92e9aaa21c25a293ce005206b0bf.jpg
Saved resized fake image to ../data_resized/1/694e3e74346e2cd12d21724dcf0f083c51934957c6675329a5211842b008acad.jpg
Saved resized fake image to ../data_resized/1/9c73ab1ef54f9b6d0b13aec6956b7e40bbba32da296416b8b1f71cdb36afbab9.jpg
Saved resized fake image to ../data_resized/1/c48491cc8410593944eda0b735d409924b84360b8e926c43f10e6097ed0ea8b4.jpg
Saved resized fake image to ../data_resized/1/be7b215d0af8f25471c04c5e5872561c24baaffbf736ff03837a28978f4550a6.jpg
Saved resized fake image to ../data_resized/1/a424a623ee4be8d36582cb3ca8d976e5acb63f7931fc1f82a7daa031ad878258.jpg
Saved resized fake image to ../data_resized/1/39b517c5d11487c00a476f86abdf0a9446f3ee9e479bbef9d682dfc4a36788a5.jpg
Saved resized fake image to ../data_resized/1/20ee29a96dc1493578a684995